### Imports

In [12]:
'''
radius .5 and symmetric inside and outside radius offsets

'''

'\nradius .5 and symmetric inside and outside radius offsets\n\n'

In [13]:
'''
Take attractor out of generative output

'''

import os
import sys
import numpy as np
import json 
import math
import random
import time
import copy
from datetime import datetime

import torch
from torch import nn
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader
from torch.utils.data.sampler import Sampler

import plotly as py
import plotly.offline as offline
import plotly.graph_objs as go
import plotly.figure_factory as ff
import plotly.io as pio

layout = go.Layout(
    height = 800,
    width = 800,
    hovermode= 'closest',
    showlegend=True,
)

CURRENT_MODEL_SAVE_DIR = './save/'
offline.init_notebook_mode(connected=True)
np.set_printoptions(precision=5, suppress=True)
print(f'pytorch={torch.__version__}, cuda={torch.version.cuda}, numpy={np.__version__}, python={sys.version}')
torch.cuda.is_available()

pytorch=1.8.0, cuda=10.2, numpy=1.19.2, python=3.8.5 (default, Sep  3 2020, 21:29:08) [MSC v.1916 64 bit (AMD64)]


True

### Code

In [14]:
class Attr_Dataset:
    def __init__(self, parms={}):
        '''
        Dataset creates a set of harmonic (multi-hand clocks)
        the output can be rotated a number of steps tp create a dynamic system
        
        '''
        #populate class variables 
        self.notes = []
        self.parms = parms
        loop_obs = parms['loop_obs']
        cycle_counts = parms['cycle_counts']
        in_radius = parms['in_radius']
        center = parms['center']
        step_offset = parms['step_offset']
        skip_loops = parms['skip_loops']
        target_radius_delta = parms['target_radius_delta']
        radius_range_offset = parms['radius_range_offset']

        if in_radius==[]:
#             in_radius = [.5, np.random.rand()*.5 + radius_range_offset]
            rand_off = np.random.rand()*radius_range_offset
            in_radius = [.5,.5+rand_off, .5-rand_off]
#         print(f'{in_radius=}')
        x_input_a,x_target_a = multi_radius_inputs_outputs(loop_obs, cycle_counts, in_radius,
                              center, step_offset,skip_loops, target_radius_delta)
        self.x_input_a = x_input_a 
        self.x_target_a = x_target_a        
        self.x_input = torch.tensor(self.x_input_a, dtype=torch.float)
        self.x_target = torch.tensor(self.x_target_a, dtype=torch.float)

        self.x_input_filter = self.x_input[:]
        self.x_target_filter = self.x_target[:]        
    
    def __getitem__(self, idx):
        return self.x_in_filter[idx], self.x_target_filter[idx]
    
    def __len__(self):
        return len(self.x_input)


In [15]:
def exists(val):
    return val is not None

#activation
class Snake(nn.Module):
    def __init__(self, alpha):
        super().__init__()
        self.a = alpha
        
    def forward(self, x):
        return x + ((torch.sin(self.a* x)) ** 2) /self.a
    
class Model(nn.Module):
    def __init__(self, input_size, hidden_size, output_size, activation):
        super(Model, self).__init__()

        # Defining some parameters
        self.input_size = input_size
        self.hidden_size = hidden_size
        self.activation = activation

        #Defining the layers
        # RNN Layer
        self.rnn = RNN(input_size, hidden_size, output_size, activation)   
        # Fully connected linear layer
        self.fc = nn.Linear(hidden_size, output_size)
    
    def forward(self, x):       
        #Initializing hidden state for first input using method defined below
        hidden = self.init_hidden(x.shape[0])

        # Passing in the input and hidden state into the model and obtaining outputs
        out, hidden = self.rnn(x, hidden)
        
        # Reshaping the outputs such that it can be fit into the fully connected layer
        out = out.contiguous().view(-1, self.hidden_size)
        out = self.fc(out)
        
        return out, hidden
    
    def init_hidden(self, input_size):
        # This method generates the first hidden state of zeros which we'll use in the forward pass
        hidden = torch.zeros(input_size, self.hidden_size).to(device)
         # We'll send the tensor holding the hidden state to the device we specified earlier as well
        return hidden
       
class RNN(nn.Module):
    # you can also accept arguments in your model constructor
    def __init__(self, data_size, hidden_size, output_size, activation):
        super(RNN, self).__init__()
        self.activation = activation
        self.hidden_size = hidden_size
        input_size = data_size + hidden_size

        self.i2h0 = nn.Linear(input_size, hidden_size)
        self.h2o0 = nn.Linear(hidden_size, output_size)
        self.i2h1 = nn.Linear(hidden_size+output_size, hidden_size)
        self.h2o1 = nn.Linear(hidden_size, output_size)

    def forward(self, data, last_hidden):
        input = torch.cat((data, last_hidden), 1)
        hidden = self.i2h0(input)
        hidden = self.activation(hidden)
        output = self.h2o0(hidden)
        output = self.activation(output)
#         print(f'1 {input.shape}{hidden.shape}{output.shape}')
        
        input = torch.cat((output, hidden), 1)
#         print(f'2 {input.shape}{hidden.shape}{output.shape}')
        hidden = self.i2h1(input)
        hidden = self.activation(hidden)
        output = self.h2o1(hidden)
        output = self.activation(output)

        return hidden, output 

class Pair_Model(nn.Module):
    def __init__(self, inputModel, outputModel):
        super(Pair_Model, self).__init__()  # just run the init of parent class (nn.Module)        
        self.inputModel = inputModel
        self.outputModel = outputModel
        
    def forward(self, x):
        x, h = self.inputModel(x)
        x, h = self.outputModel(x)       
        return x, h

In [16]:
def multi_radius_inputs_outputs2D(loop_obs=10,in_radius=[.4, .5], target_radius_delta=0.3, step_offset=1,center=.5):
    '''
    target radius i calculated to point inward from outside .5 and outward inside .5
    target_radius_delta = 0 will cause output and input radius to be the same
    a positive number indicates the power of the attractor around .5
    
    radius_range_offset is not being used and needs to be removed, it has been moved to the dataset class
    to control the distribution of random input radiuses that are paired with a .5 radius if the input radius spec is empty
    '''

    inList=[]
    targetList=[]
    angles = np.linspace(0, 2*math.pi, loop_obs+1)[:-1] #remove overlap start/finish
#     print(in_radius)
    for radius in in_radius:
        target_radius = target_radius_delta*(.5-radius)+radius
#         print(f'{target_radius_delta=}{target_radius=}')
        
        cd_in  = get_circle_data(loop_obs, radius)
        cd_target  = get_circle_data(loop_obs, target_radius)
        cd_target = get_circle_offset(cd_target,step_offset)
        
        inList.append(cd_in)
        targetList.append(cd_target)
        
    return np.array(inList), np.array(targetList)

def get_circle_data(loop_obs=30, radius=.5, center=[.5,.5]):
    a = np.linspace(0,1,loop_obs+1)*2*math.pi
    a = np.dstack([np.sin(a),np.cos(a)])[0]
    return (radius*a+center)[:-1]

def get_circle_offset(circle,step_offset=0):
    return np.concatenate([circle[step_offset:],circle[:step_offset]])

def multi_radius_inputs_outputs(loop_obs, cycle_counts,  in_radius, center,step_offset,skip_loops,target_radius_delta):
    '''
    '''    
    #calc cumulative cycles
    cycles = [1] #initialize first cycle (should be one for unity across all cycles)
    for i, n in enumerate(cycle_counts[1:]):
        cycles.append(cycles[i]*n)
    total_obs = cycles[-1]*loop_obs
    
    #calc cumulative num obs
    cycle_obs = []
    for n in cycles:
        cycle_obs.append(total_obs//n)
    
    xilist = []
    xtlist = []
    for co in cycle_obs:
        x_input_a,x_target_a = multi_radius_inputs_outputs2D(co, in_radius, 
                                  target_radius_delta,step_offset, center)
        xilist.append(x_input_a)
        xtlist.append(x_target_a)
        
    xlist = []
    tlist = []
    for i, c in enumerate(cycles):
        xi = np.array(xilist[i])
        xt = np.array(xtlist[i])
        for ii in range(c-1):
            xi = np.concatenate([xi,xilist[i]],1)
            xt = np.concatenate([xt,xtlist[i]],1)
            
        ###################### xlist contains different shapes
        xlist.append(xi[:,loop_obs*skip_loops:,:])
        tlist.append(xt[:,loop_obs*skip_loops:,:])
    x_input = np.reshape(xlist,[len(cycles),-1,2])
    x_target = np.reshape(tlist,[len(cycles),-1,2])
    
    if len(cycles) ==1:
        #two harmonics
        return x_input[0], x_target[0]
    if len(cycles) ==2:
        #two harmonics
        x_input_a = np.concatenate([x_input[0],x_input[1]],1)
        x_target_a = np.concatenate([x_target[0],x_target[1]],1)
    elif len(cycles) ==3:      
        #three harmonics
        x_input_a = np.concatenate([x_input[0],x_input[1],x_input[2]],1)
        x_target_a = np.concatenate([x_target[0],x_target[1],x_target[2]],1)
    elif len(cycles) ==4:        
        #three harmonics
        x_input_a = np.concatenate([x_input[0],x_input[1],x_input[2],x_input[3]],1)
        x_target_a = np.concatenate([x_target[0],x_target[1],x_target[2],x_target[3]],1)
    else:
        print('unsupported number of cycles')
        
    return x_input_a, x_target_a

In [17]:
def set_random_seed(seed, deterministic=False):
    """Set random seed.

    Args:
        seed (int): Seed to be used.
        deterministic (bool): Whether to set the deterministic option for
            CUDNN backend, i.e., set `torch.backends.cudnn.deterministic`
            to True and `torch.backends.cudnn.benchmark` to False.
            Default: False.
    """
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
    if deterministic:
        torch.backends.cudnn.deterministic = True
        torch.backends.cudnn.benchmark = False

def graph_curves(xyCurves, layout=go.Layout(),labels=[], dashRange=range(0,0), mode='lines+markers'):
    traces = []
    for i in range (0, len(xyCurves)):
        xyCa = np.array(xyCurves[i])
        if i < len(labels):
            label = labels[i]
        else:
            label = str(i)
            
        #create a line/spline for each curve   
        sc = go.Scatter(
            x =  xyCa[0]
            ,y = xyCa[1]
            ,name = label
            ,line = dict(shape='spline')  
            )
        #add dash attributes if within dashRange
        sc.mode=mode
        if i in dashRange:
            sc.line['dash'] = '2px,6px'
            sc.marker['symbol'] = 'star'
            
        traces.append(sc)
    return go.Figure(data=traces, layout=layout)


def add_trace(subplot,trace,row,col):
    for d in trace.data:
        subplot.add_traces(d, rows=[row], cols=[col])
    return

def graph_quiver(x_input_a,pred,dims,name,scale=.8, arrow_scale=.3):
    xi = x_input_a[:,dims]
    xt = pred[:,dims]
    uv = xt-xi;
    x= xi[:,0];y= xi[:,1];u = uv[:,0];v = uv[:,1];
    qt = ff.create_quiver(x, y, u, v,
            scale=scale,
            arrow_scale=arrow_scale,
            name=name,
          )
    return qt

def x_unflatten(x,num_attractors,num_cycles):
    feature_size = x.shape[-1]
    return np.reshape(x,[num_attractors,num_cycles,-1,feature_size])

### Data

In [18]:
'''
Calculate Datasets from parameters and input character dataset

'''
loop_obs = 42
skiploops = 0

parmsT = {
    'loop_obs':loop_obs,
    'in_radius':[],
    'cycle_counts':[1,2,2,2],
    'target_radius_delta': .2, 
    'radius_range_offset': .2, #how far inside/outside circle
    'skip_loops':skiploops,
    'step_offset':1,
    'center':0.5
    }
datasetT = Attr_Dataset(parmsT)

parmsL = copy.deepcopy(parmsT)
parmsL['in_radius'] = []
# parmsL['out_radius'] = [0.49, 0.51]
parmsL['skip_loops'] = 0
datasetL = Attr_Dataset(parmsL)

datasetT.x_input_filter.shape, datasetT.x_target_filter.shape, datasetL.x_input_a.shape, parmsT

(torch.Size([1008, 8]),
 torch.Size([1008, 8]),
 (1008, 8),
 {'loop_obs': 42,
  'in_radius': [],
  'cycle_counts': [1, 2, 2, 2],
  'target_radius_delta': 0.2,
  'radius_range_offset': 0.2,
  'skip_loops': 0,
  'step_offset': 1,
  'center': 0.5})

In [19]:
'''
Recalc datasetT to get different randomly generated training radiuses
use datasetL to get narrow inner and outer boundaries arround attractor field (used for loss calc)

'''

ds = datasetT
# ds = datasetL
# ds = datasetE

xi = ds.x_input_a
xtt = ds.x_target_a
f,t = loop_obs*0, loop_obs*120000

gqi01 = graph_quiver(xi[f:t],xtt[f:t],[0,1],'gqi01',.99)
gqi23 = graph_quiver(xi[f:t],xtt[f:t],[4,5],'gqi23',.99)
gqi02 = graph_quiver(xi[f:t],xtt[f:t],[2,4],'gqi02',.99)
gqi03 = graph_quiver(xi[f:t],xtt[f:t],[1,7],'gqi03',.99)

# tl = [str(parms['in_radius']), str(parms['out_radius'])]
pp_attractor = py.subplots.make_subplots(rows=1, cols=4) #,subplot_titles = tl)                                                                        
add_trace(pp_attractor,gqi01,row=1,col=1)
add_trace(pp_attractor,gqi23,row=1,col=2)
add_trace(pp_attractor,gqi02,row=1,col=3)
add_trace(pp_attractor,gqi03,row=1,col=4)

####

pp_attractor.layout.xaxis.range = [-.1,1.1]
pp_attractor.layout.yaxis.range = [-.1,1.1]
pp_attractor.update_layout(template='simple_white',height=350, width=1000,showlegend=True, title=f'' )
pp_attractor

In [20]:
f,t = 42*8*1, 42*8*1+42

gq = graph_quiver(xi[f:t],xtt[f:t],[6,7],'gqi23',.99)
gq.layout.width = 500
gq.layout.height = 500
gq
# xi.shape

### Train

In [21]:
'''
'''
############################################
train=False
device = 'cpu'
set_random_seed(43, deterministic=True)
print(f'{device=}, {train=}')
# net_shape = [[8,40,50],[50,20,8]]

activation = Snake(2)
net_shape = [[8,30,40],[40,20,8]]
e_model = Model(input_size=8, hidden_size=30, output_size=40, activation=activation)
da_model = Model(input_size=40, hidden_size=20, output_size=8, activation=activation)
model = Pair_Model(e_model,da_model)
loss_fn = nn.SmoothL1Loss()

parmsT['activation'] = 'Snake(2)'
parmsT['loss_fn'] = 'nn.SmoothL1Loss()'
parmsT['net_shape'] = net_shape
cnt = 0

# datasetT.x_input_filter.shape, datasetT.x_target_filter.shape, parmsT
e_model, parmsT

device='cpu', train=False


(Model(
   (activation): Snake()
   (rnn): RNN(
     (activation): Snake()
     (i2h0): Linear(in_features=38, out_features=30, bias=True)
     (h2o0): Linear(in_features=30, out_features=40, bias=True)
     (i2h1): Linear(in_features=70, out_features=30, bias=True)
     (h2o1): Linear(in_features=30, out_features=40, bias=True)
   )
   (fc): Linear(in_features=30, out_features=40, bias=True)
 ),
 {'loop_obs': 42,
  'in_radius': [],
  'cycle_counts': [1, 2, 2, 2],
  'target_radius_delta': 0.2,
  'radius_range_offset': 0.2,
  'skip_loops': 0,
  'step_offset': 1,
  'center': 0.5,
  'activation': 'Snake(2)',
  'loss_fn': 'nn.SmoothL1Loss()',
  'net_shape': [[8, 30, 40], [40, 20, 8]]})

In [22]:
# '''
# training loop

# '''
parmsT['net_shape'] = net_shape

# epochs = 5
# epochs = 100
epochs = 1000

lr = .005
# lr=0.003
# lr=0.001
# lr=0.0001
# lr=0.00001
# lr=0.000001

optimizer = torch.optim.Adam(model.parameters(), lr=lr)
if train:
    min_loss = 1000
    max_loss = 0
    start = time.time()
    for epoch in range(epochs):
        optimizer.zero_grad() # Clears existing gradients from previous epoch
        datasetT = Attr_Dataset(parmsT)
        output, hidden = model(datasetT.x_input_filter)
        target = datasetT.x_target_filter.to(device)

        loss = loss_fn(output, target) # loss = criterion(output, target_seq.view(-1).long())
        if loss < min_loss: min_loss = loss
        if loss > max_loss: max_loss = loss

        loss.backward() # Do backpropagation and calculates gradients
        optimizer.step() # Updates the weights accordingly
        if epoch % (epochs/10) == 0:
            loss = loss_fn(output, target)
            print(f'{cnt=}, {loss.data:.7f}')
        cnt+=1

    print(parmsT)
    print(f'epochs={cnt}, loss={loss.data*100000:.4f}, min loss={min_loss.data*100000:.4f}, max loss={max_loss.data*100000:.2f}, {lr=}')
    print('\ntime: {0:.2f}'.format( time.time()-start))

else:
    fname = '1-2-2-2 cycle attractor'
    PATH = CURRENT_MODEL_SAVE_DIR + fname + '.cfg'
    with open(PATH, 'r') as fp:
        parmsT = json.load(fp)
    print(PATH, '\n',parmsT)
        
    PATH = CURRENT_MODEL_SAVE_DIR + fname + 'E.pth'
    with open(PATH, 'r') as fp:
        e_model.load_state_dict(torch.load(PATH)) 
        
    PATH = CURRENT_MODEL_SAVE_DIR + fname + 'DA.pth'
    with open(PATH, 'r') as fp:
        da_model.load_state_dict(torch.load(PATH))

    model = Pair_Model(e_model,da_model)


./save/1-2-2-2 cycle attractor.cfg 
 {'loop_obs': 42, 'in_radius': [], 'cycle_counts': [1, 2, 2, 2], 'target_radius_delta': 0.3, 'radius_range_offset': 0.2, 'skip_loops': 0, 'step_offset': 1, 'center': 0.5, 'activation': 'Snake(2)', 'loss_fn': 'nn.SmoothL1Loss()', 'net_shape': [[8, 30, 40], [40, 20, 8]], 'hash': 8266831400117947739, 'fname': '1-2-2-2 cycle attractor', 'save_time': 'December 06 2021 20:55'}


In [23]:
'''
{'loop_obs': 42, 'in_radius': [], 'cycle_counts': [1, 2, 2, 2], 'target_radius_delta': 0.2, 'radius_range_offset': 0.2, 'skip_loops': 0, 'step_offset': 1, 'center': 0.5, 'activation': 'Snake(2)', 'loss_fn': 'nn.SmoothL1Loss()', 'net_shape': [[8, 30, 40], [40, 20, 8]]}
epochs=1000, loss=8.5450, min loss=2.4869, max loss=17623.12, lr=0.005
epochs=2000, loss=3.3634, min loss=1.3373, max loss=8382.81, lr=0.005
epochs=3000, loss=3.9684, min loss=0.7264, max loss=10959.21, lr=0.005

epochs=1000, loss=8.3916, min loss=2.6105, max loss=17621.94, lr=0.005
epochs=2000, loss=4.3253, min loss=1.2354, max loss=7830.48, lr=0.005
epochs=3000, loss=4.1584, min loss=0.6500, max loss=6970.49, lr=0.005 9864
epochs=4000, loss=0.8183, min loss=0.3472, max loss=5795.76, lr=0.005 9997
epochs=6000, loss=0.5308, min loss=0.1697, max loss=1644.80, lr=0.003 9997
epochs=7000, loss=0.1260, min loss=0.0930, max loss=142.16, lr=0.001 9999

'''
pass

### Evaluate

In [24]:
'''


'''
rrange = 2000
# rrange = 13000

parmsE = copy.deepcopy(parmsT)
# parmsE['in_radius'] = [0.46, 0.54]
parmsE['in_radius'] = [.3, 0.46, 0.54, .7]
parmsE['skip_loops'] = 0
datasetE = Attr_Dataset(parmsE)

input_dims = datasetE.x_input.shape[1]
xe_input_a = datasetE.x_input_a
xe_hat, _ = model(datasetE.x_input)
xe_hat_a = xe_hat.detach().numpy()

#recursive path through attractor (output -> input)
r_input = datasetE.x_input[0]+torch.ones([input_dims],dtype=torch.float)*0
print(r_input)
r_outL = [r_input.detach().numpy()] #start point
r_input = r_input.unsqueeze(0)
for i in range(rrange):
    r_out, _ = model(r_input)
    r_outL.append(r_out[0].detach().numpy())
    r_input = r_out
r_outA = np.array(r_outL)

xe_hat_a.shape, r_outA.shape, 

tensor([0.5000, 0.8000, 0.5000, 0.8000, 0.5000, 0.8000, 0.5000, 0.8000])


((1344, 8), (2001, 8))

In [25]:
inperiod = False
inpoint = False
inattract = False
lastperiodi = 999
minn= 1000
tolerance = .002
# tolerance = .0015
# tolerance = .001
# tolerance = .0001

print(r_outA[-1])
for i in range(r_outA.shape[0]):
    dif = r_outA[-1] - r_outA[i]
    sq = np.square(dif)
    maxx = np.max(sq)
    if maxx < minn: 
#         print(i,'mim max: \n',dif,'\n',sq,'\n',maxx)
        minn = maxx
    if maxx < tolerance:
        inattract = True
        if lastperiodi == 999: 
            print(i,f'{inattract=}')
            lastperiodi = i
        print(i,f'period: {i-lastperiodi}')
        lastperiodi = i
    if (inattract == True) and np.max(np.square(r_outA[i]-r_outA[i-5])) < tolerance:
        print(i, 'in point attractor','\n',r_outA[i])
        break
    if (inattract == True) and maxx>minn:
        inperiod = True
#         lastperiodi = i
#         print('in loop:', i)


[0.4052  0.99729 0.32079 0.95398 0.1586  0.86436 0.00599 0.53994]
325 inattract=True
325 period: 0
660 period: 335
995 period: 335
1330 period: 335
1665 period: 335
2000 period: 335


In [26]:
f,t = loop_obs*0, loop_obs*180
ri = r_outA[:-1]
rt = r_outA[1:]

layout3D = go.Layout(
     width = 600,
     height = 600,
     title = '',
     showlegend=True,
    scene = dict(
        xaxis = dict(nticks=4, range=[-.3,1.3]),
        yaxis = dict(nticks=4, range=[-.3,1.3],),
        zaxis = dict(nticks=4, range=[-.3,1.3],),
    ))
# f3d = go.Scatter3d(x=rt[:,1], y=rt[:,2], z=rt[:,3], mode='lines+markers', marker=dict(symbol='circle', size=2))
# f3d = go.Scatter3d(x=rt[:,0], y=rt[:,2], z=rt[:,3], mode='lines+markers', marker=dict(symbol='circle', size=2))
f3d = go.Scatter3d(x=rt[:,0], y=rt[:,4], z=rt[:,7], mode='lines+markers', marker=dict(symbol='circle', size=2))
# f3d = go.Scatter3d(x=rt[f:,0], y=rt[f:,5], z=rt[f:,7], mode='lines', marker=dict(symbol='circle', size=2))
ff3d = go.Figure(data=[f3d])
camera = dict(
#     eye=dict(x=1, y=-1, z=1.))
    eye=dict(x=.06, y=-.06, z=-1.7))

ff3d.update_layout(scene_camera=camera)
ff3d

In [27]:
# ff3d
# PATH = "./image/3d attractor 2-6-strange e7000.png"
# ff3d.write_image(PATH)


In [28]:
'''
Calculate evaluation data
Two attractors

'''
# xi = datasetL.in_filter_a
xi = datasetE.x_input_a
xtt = xe_hat_a

# dims = [0,1]
dims = [2,3]
dims = [4,5]
gr = graph_quiver(xi[f:t],xtt[f:t],dims,'gqi01',.9,.4)
gr.update_layout(template='simple_white',height=600, width=600,showlegend=True, title=f'{lr=}, {cnt=}' )
gr

In [29]:
# xi = datasetE.x_input_a
# xtt = xe_hat_a

f,t = loop_obs*0, loop_obs*24
ri = r_outA[:-1]
rt = r_outA[1:]

gqi01 = graph_quiver(xi[f:t],xtt[f:t],[2,3],'gqi01',.99)
gqi23 = graph_quiver(xi[f:t],xtt[f:t],[4,5],'gqi23',.99)
gqi12 = graph_quiver(ri[f:t],rt[f:t],[0,1],'gqi45',.99,.1)

###
f,t = loop_obs*0, loop_obs*50
gqr01 = graph_quiver(ri[f:t],rt[f:t],[2,3],'gqr01',.99,.1)
gqr23 = graph_quiver(ri[f:t],rt[f:t],[4,5],'gqr23',.99,.1)
gqr12 = graph_quiver(ri[f:t],rt[f:t],[6,7],'gqr12',.99,.1)

# gqi01 = graph_quiver(xi[f:t],xtt[f:t],[0,1],'gqi01',.99)
# gqi23 = graph_quiver(xi[f:t],xtt[f:t],[0,5],'gqi23',.99)
# gqi12 = graph_quiver(xi[f:t],xtt[f:t], [0,7],'gqi45',.99,.1)

# ###
# f,t = loop_obs*0, loop_obs*50
# gqr01 = graph_quiver(ri[f:t],rt[f:t],[0,1],'gqr01',.99,.1)
# gqr23 = graph_quiver(ri[f:t],rt[f:t],[0,5],'gqr23',.99,.1)
# gqr12 = graph_quiver(ri[f:t],rt[f:t],[0,7],'gqr12',.99,.1)

##
tl = [f'Start point: {ri[0,0:2]}']
pp_attractor = py.subplots.make_subplots(rows=2, cols=4,subplot_titles = tl)                                                                        
add_trace(pp_attractor,gqi01,row=1,col=1)
add_trace(pp_attractor,gqi23,row=1,col=2)
add_trace(pp_attractor,gqi12,row=1,col=3)

add_trace(pp_attractor,gqr01,row=2,col=1)
add_trace(pp_attractor,gqr23,row=2,col=2)
add_trace(pp_attractor,gqr12,row=2,col=3)

pp_attractor.layout.xaxis.range = [-.1,1.1]
pp_attractor.layout.yaxis.range = [-.1,1.1]
pp_attractor.update_layout(template='simple_white',height=800, width=1200,showlegend=True, title=f'{lr=}, {cnt=}' )
pp_attractor

### Save

In [30]:
%%javascript
IPython.notebook.kernel.execute(`notebookName = '${window.document.getElementById("notebook_name").innerHTML}'`);

<IPython.core.display.Javascript object>

In [31]:
# fname = notebookName# +'-e3200'

# hash0 = hash(str(parmsT))
# parmsT['hash'] = hash0
# parmsT['fname'] = fname
# parmsT['activation'] =  'Snake(2)'
# parmsT['save_time'] = time.strftime("%B %d %Y %H:%M", time.localtime())

# PATH = CURRENT_MODEL_SAVE_DIR + fname + '.cfg'
# with open(PATH,'w') as f:
#     json.dump(parmsT,f)

# # PATH = "./image/3d attractor-" + str(hash0) + ".png"
# # ff3d.write_image(PATH)

# # PATH = "./image/attractor-" + str(hash0) + ".png"
# # pp_attractor.write_image(PATH)

# PATH = CURRENT_MODEL_SAVE_DIR + fname + 'E.pth'
# torch.save(e_model.state_dict(), PATH)

# PATH = CURRENT_MODEL_SAVE_DIR + fname + 'DA.pth'
# torch.save(da_model.state_dict(), PATH)

# PATH, parmsT

In [32]:
'''
('./save/1-2-2-2 cycle attractorDA.pth',
 {'loop_obs': 42,
  'in_radius': [],
  'cycle_counts': [1, 2, 2, 2],
  'target_radius_delta': 0.3,
  'radius_range_offset': 0.2,
  'skip_loops': 0,
  'step_offset': 1,
  'center': 0.5,
  'activation': 'Snake(2)',
  'loss_fn': 'nn.SmoothL1Loss()',
  'net_shape': [[8, 30, 40], [40, 20, 8]],
  'hash': 8266831400117947739,
  'fname': '1-2-2-2 cycle attractor',
  'save_time': 'December 06 2021 20:55'})
  
'''
pass

In [80]:
'''

'''
fullPath = CURRENT_MODEL_SAVE_DIR +'blend_in2.json'
with open(fullPath, 'r') as fp:
    ch2 = json.load(fp)
    ch2aa = np.array(ch2)
# blend_in.shape, fullPath

fname = 'blend_out.json'
PATH = CURRENT_MODEL_SAVE_DIR + fname
with open(PATH, 'r') as fp:
    ch = json.load(fp)
    chaa = np.array(ch)
    chaa = np.array(chaa[0:1,:,:,:])
print(PATH, '\n',chaa.shape,ch2aa.shape)
# (1, 25, 3, 3) (1, 22, 3, 3) strokes, obs, lines, xyz

cha = chaa
cha = ch2aa

st0 = cha[0,:,0,:] #(25, 3)
sta0 = np.array([st0[:,0],st0[:,1]])

st1 = cha[0,:,1,:] #(25, 3)
sta1 = np.array([st1[:,0],st1[:,1]])

st2 = cha[0,:,2,:] #(25, 3)
sta2 = np.array([st2[:,0],st2[:,1]])

graph_curves([sta0, sta1, sta2])

./save/blend_in.json 
 (1, 25, 3, 3) (1, 22, 3, 3)


In [85]:


# [st[:,0],st[:,1]]
# sta

In [86]:
blend_x = np.array(cha)
fullPath = CURRENT_MODEL_SAVE_DIR +'blend_x.json'
with open(fullPath, 'w') as fp:
    json.dump(blend_x.tolist(),fp)
    
blend_x.shape, fullPath

((1, 22, 3, 3), './save/blend_x.json')